In [1]:
!pip install xlrd
!pip install geopandas
!pip install openpyxl

In [2]:
import pandas as pd
import folium  #needed for interactive map
from folium import IFrame
from folium.plugins import MarkerCluster 
import geopandas as gpd
#import shapefile as shp
from folium import FeatureGroup, LayerControl

In [3]:
#Read Data Clean
df_airbnb=pd.read_csv('Aribnblocalidades.csv')
df_crimenes=pd.read_csv('DeitosLocalidades.csv',encoding='latin1')
df_Transmilenios=pd.read_csv('TMLocalidades.csv',encoding='latin1')
df_banks=pd.read_csv('bankslocalidades.csv',encoding='latin1')
df_ATM=pd.read_csv('ATMsLocalidades.csv',encoding='latin1') 
df_pharmacies=pd.read_csv('PharmaciesLocalidades.csv',encoding='latin1') 
df_health=pd.read_csv('healthlocalidades.csv',encoding='latin1') 
df_turistic_places=pd.read_csv('7. Base de Atractivos turísticos (2021).csv',encoding='latin1')
#df_wifi=pd.read_csv('8. Base de puntos de WiFi gratuitos en Bogotá (2021).csv', delimiter=',',encoding='latin1')
#df_SITP=pd.read_csv('9. Base de las rutas de transporte e Bogotá (2021)- Paraderos Zonales SITP.csv',encoding='latin1')

/opt/conda/lib/python3.8/site-packages/IPython/core/interactiveshell.py:3165: DtypeWarning: Columns (5,15,30,42,43,51,52) have mixed types.Specify dtype option on import or set low_memory=False.
  has_raised = await self.run_ast_nodes(code_ast.body, cell_name,


In [4]:
df_turistic_places['color']=df_turistic_places['Tipo de Patrimonio'].replace({'Patrimonio cultural material inmueble':'lightblue',
                                                                             'Patrimonio cultural inmaterial':'lightred',
                                                                              'Áreas protegidas':'orange',
                                                                              'Patrimonio Cultural Mueble':'green',
                                                                              'Aguas lénticas':'pink',
                                                                              'Montañas':'lightgreen',
                                                                              'Aguas lóticas':'lightgray',
                                                                              'Formaciones cársicas':'gray'
                                                                              }
                                                                            )
#https://matplotlib.org/3.5.0/gallery/color/named_colors.html página de colores

In [5]:
#Define Icons

df_turistic_places['icon']=df_turistic_places['color']
#https://matplotlib.org/3.5.0/gallery/color/named_colors.html página de colores

for i in range(0,len(df_turistic_places)):
    if df_turistic_places.iloc[i]['Tipo de Patrimonio']=='Patrimonio cultural material inmueble':
        df_turistic_places['icon'].iloc[i]="globe"
        
    if df_turistic_places.iloc[i]['Tipo de Patrimonio']=='Patrimonio cultural inmaterial':
        df_turistic_places['icon'].iloc[i]="paint-brush"
        
    if df_turistic_places.iloc[i]['Tipo de Patrimonio']=='Áreas protegidas':
        df_turistic_places['icon'].iloc[i]="tree"
        
    if df_turistic_places.iloc[i]['Tipo de Patrimonio']=='Patrimonio Cultural Mueble':
        df_turistic_places['icon'].iloc[i]="institution"
        
    if df_turistic_places.iloc[i]['Tipo de Patrimonio']=='Aguas lénticas':
        df_turistic_places['icon'].iloc[i]="pagelines"
        
    if df_turistic_places.iloc[i]['Tipo de Patrimonio']=='Montañas':
        df_turistic_places['icon'].iloc[i]="toggle-up"
        
    if df_turistic_places.iloc[i]['Tipo de Patrimonio']=='Aguas lóticas':
        df_turistic_places['icon'].iloc[i]="life-bouy"
        
    if df_turistic_places.iloc[i]['Tipo de Patrimonio']=='Formaciones cársicas':
        df_turistic_places['icon'].iloc[i]="sun-o"
#https://fontawesome.com/v4/icons/

/home/jovyan/.local/lib/python3.8/site-packages/pandas/core/indexing.py:1637: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_single_block(indexer, value, name)


In [6]:
poligonos=gpd.read_file('/home/jovyan/DataBases-Estefania/poligonos-localidades.shp',encoding='UTF-8')
#poligonos
#https://bogota-laburbano.opendatasoft.com/explore/dataset/poligonos-localidades/export/?flg=es

In [7]:
#Crear Mapa
map = folium.Map(location=[4.60971,-74.08175], tiles='CartoDB positron')

lista=range(1,poligonos.shape[0]+1)
j=3

#Mostrar Polígono
for _, r in poligonos.iterrows():
    sim_geo = gpd.GeoSeries(r['geometry']).simplify(tolerance=0.001)
    geo_j = sim_geo.to_json()
    geo_j = folium.GeoJson(data=geo_j,
                           style_function=lambda x: {'fillColor': 'blue'})
    folium.Popup(r['Nombre_de_l']).add_to(geo_j)
    geo_j.add_to(map)
    j=j+1
    
#Puntos Turísticos
i=0
for _, r in df_turistic_places.iterrows():
    html=f"""
    <h1> {df_turistic_places.iloc[i]['Tipo de Patrimonio']}</h1>
    <p></p>
    {df_turistic_places.iloc[i]['Nombre']}
    <li>{df_turistic_places.iloc[i]['Direccion Atractivo']}</li>
    </ul>
    </p>
    """
    icon=df_turistic_places.iloc[i]['icon']
    
    lat = r['Latitud']
    lon = r['Longitud']
    folium.Marker(location=[lat, lon],
                  popup=html,
                  icon=folium.Icon(color='catedblue', icon=icon,prefix='fa'),
                 ).add_to(map)
    i=i+1

#Puntos Pharmacies
i=0
for _, r in df_pharmacies.iterrows():
    
    nombre=df_pharmacies.iloc[i]['farmacia']
    
    lat = r['latitud']
    lon = r['longitud']
    folium.Marker(location=[lat, lon],
                  popup=nombre,
                  icon=folium.Icon(color='beige', icon='medkit',prefix='fa'),
                 ).add_to(map)
    i=i+1

#Puntos ATM
i=0
for _, r in df_ATM.iterrows():
    
    nombre=df_ATM.iloc[i]['atm_name']
    
    lat = r['atm_latitude']
    lon = r['atm_longitude']
    folium.Marker(location=[lat, lon],
                  popup=nombre,
                  icon=folium.Icon(color='lightred', icon='bank',prefix='fa'),
                 ).add_to(map)
    i=i+1

#Puntos Airbnb
i=0
for _, r in df_airbnb.iterrows():
    
    nombre=df_airbnb.iloc[i]['Listing Title']
    
    lat = r['Latitude']
    lon = r['Longitude']
    folium.Marker(location=[lat, lon],
                  popup=nombre,
                  icon=folium.Icon(color='lightred', icon='bank',prefix='fa'),
                 ).add_to(map)
    i=i+1

map

<ipython-input-7-e90064947430>:21: UserWarning: color argument of Icon should be one of: {'lightgray', 'white', 'gray', 'red', 'pink', 'darkred', 'lightblue', 'darkblue', 'purple', 'beige', 'green', 'lightgreen', 'darkpurple', 'blue', 'black', 'lightred', 'orange', 'darkgreen', 'cadetblue'}.
  icon=folium.Icon(color='catedblue', icon=icon,prefix='fa'),
<ipython-input-7-e90064947430>:35: UserWarning: color argument of Icon should be one of: {'lightgray', 'white', 'gray', 'red', 'pink', 'darkred', 'lightblue', 'darkblue', 'purple', 'beige', 'green', 'lightgreen', 'darkpurple', 'blue', 'black', 'lightred', 'orange', 'darkgreen', 'cadetblue'}.
  icon=folium.Icon(color='catedblue', icon='medkit',prefix='fa'),


In [ ]:
map.save('FinalMap.html')
